In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import datetime as dt
import itertools
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error

In [2]:
#importing encoded, transformed and standardized data

path = './'
std_ft_df = pd.read_csv(path+'std_ft_df.csv')
print('\nNumber of rows and columns in the data set: ',std_ft_df.shape)


Number of rows and columns in the data set:  (27820, 17)


In [5]:
#X/y Split
X = std_ft_df.drop('suicides/100k pop',axis=1) # Independent variable
y = std_ft_df['suicides/100k pop'] # dependent variable

In [6]:
all_data = [X] 
all_label = [y] 
result = {}
model_max_depth_4 = []
param_grid = {'max_depth': [4, 8, 15, 25, 30],
              'n_estimators': [30, 50, 70, 90, 110],
              'max_features': [0.1, 0.3, 0.5, 0.7, 0.9]}
all_param_combo = list(itertools.product(param_grid['max_depth'], param_grid['n_estimators'], param_grid['max_features']))
print(all_param_combo)
for data, label in zip(all_data, all_label):
    # when using the out of bags trick, it is not neccesary to split the dataset.

    for param in tqdm(all_param_combo):
        rf = RandomForestRegressor(max_depth=param[0], n_estimators=param[1], max_features=param[2], oob_score=True)
        rf.fit(data, label)
        result[param]=rf.oob_score_

        # save the model for Question 23
        if param[0]==4:
            model_max_depth_4.append(rf)

  1%|          | 1/125 [00:00<00:18,  6.72it/s]

[(4, 30, 0.1), (4, 30, 0.3), (4, 30, 0.5), (4, 30, 0.7), (4, 30, 0.9), (4, 50, 0.1), (4, 50, 0.3), (4, 50, 0.5), (4, 50, 0.7), (4, 50, 0.9), (4, 70, 0.1), (4, 70, 0.3), (4, 70, 0.5), (4, 70, 0.7), (4, 70, 0.9), (4, 90, 0.1), (4, 90, 0.3), (4, 90, 0.5), (4, 90, 0.7), (4, 90, 0.9), (4, 110, 0.1), (4, 110, 0.3), (4, 110, 0.5), (4, 110, 0.7), (4, 110, 0.9), (8, 30, 0.1), (8, 30, 0.3), (8, 30, 0.5), (8, 30, 0.7), (8, 30, 0.9), (8, 50, 0.1), (8, 50, 0.3), (8, 50, 0.5), (8, 50, 0.7), (8, 50, 0.9), (8, 70, 0.1), (8, 70, 0.3), (8, 70, 0.5), (8, 70, 0.7), (8, 70, 0.9), (8, 90, 0.1), (8, 90, 0.3), (8, 90, 0.5), (8, 90, 0.7), (8, 90, 0.9), (8, 110, 0.1), (8, 110, 0.3), (8, 110, 0.5), (8, 110, 0.7), (8, 110, 0.9), (15, 30, 0.1), (15, 30, 0.3), (15, 30, 0.5), (15, 30, 0.7), (15, 30, 0.9), (15, 50, 0.1), (15, 50, 0.3), (15, 50, 0.5), (15, 50, 0.7), (15, 50, 0.9), (15, 70, 0.1), (15, 70, 0.3), (15, 70, 0.5), (15, 70, 0.7), (15, 70, 0.9), (15, 90, 0.1), (15, 90, 0.3), (15, 90, 0.5), (15, 90, 0.7), (15,

 61%|██████    | 76/125 [02:49<03:53,  4.78s/it]C:\Users\ohass\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py:832: UserWarning: Some inputs do not have OOB scores. This probably means too few trees were used to compute any reliable oob estimates.
  warn("Some inputs do not have OOB scores. "
100%|██████████| 125/125 [06:43<00:00,  3.23s/it]


#### Question 23
Randomly pick a tree in your random forest model (with maximum depth of 4) and
plot its structure. Which feature is selected for branching at the root node? What
can you infer about the importance of features? Do the important features match
what you got in part 4.2.1?

In [31]:

# random forest visualize
from sklearn import tree


fig, axes = plt.subplots(nrows = 1,ncols = 1,figsize = (28,10), dpi=900)
tree.plot_tree(model_max_depth_4[0].estimators_[0],
               feature_names = X.columns, 
               class_names='total count',
               filled = True,
               fontsize=11);

In [37]:
features_importance = rf.feature_importances_
feature_names = X.columns

print("Feature ranking:")
for i, data_class in enumerate(feature_names):
    print("{}. {} ({})".format(i + 1, data_class, features_importance[i]))


Feature ranking:
1. yr_bc_std (0.18628673946736757)
2. gdpc_bc_std (0.0742753158781868)
3. gdpyr_bc_std (0.20021202259209592)
4. age_std (0.12493014195218152)
5. pop_bc_std (0.14186817203904412)
6. continent_Asia (0.02265778552016983)
7. continent_Europe (0.028233523035964797)
8. continent_North America (0.022498767822449674)
9. continent_Oceania (0.003655499855463336)
10. continent_South America (0.01641130993845634)
11. sex_male (0.15836052336943016)
12. generation_G.I. Generation (0.0065453217297075485)
13. generation_Generation X (0.0019127953196749798)
14. generation_Generation Z (0.0020444090870838836)
15. generation_Millenials (0.005477285418552478)
16. generation_Silent (0.004630386974171034)


#### At the root node, the model selected a One-Hot encoded feature: "generation_G.I. Generation" for branching; which has one of the lowest importance scores in this model and has a high p-value in the LR model.  The top 2 important features with the RandomForest model are "gdp/yr" &  "year". This partially matches the highest Theta features from Linear Regression: "sex_male" & "year". The 2 models agree on the importance of "year" as a feature. RF ranks "sex_male" as the 3rd most importance while LR ranks "gdp/yr" as 8th most important out of 17. So the models agree on the importance of "year" & "sex_male" but disagree on "gdp/yr".

In [34]:
from sklearn.model_selection import cross_validate
import numpy as np
   
#10-fold cross-validation for Random Forest Regression
cv_results = cross_validate(rf,X,y,scoring='neg_root_mean_squared_error',cv=10,return_train_score=True,return_estimator=True)
train_rmse = np.sqrt(cv_results['train_score']*(-1.))
test_rmse = np.sqrt(cv_results['test_score']*(-1.))
print("Average Train RMSE for Random Forest Regression:", np.mean(train_rmse))
print("Average Test RMSE for Random Forest Regression:", np.mean(test_rmse))

Average Train RMSE for Random Forest Regression: 1.6265833523575313
Average Test RMSE for Random Forest Regression: 4.016867002715296
